----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------
# IBM Data Science 
## Capstone Project
### *Applied Data Science Capstone - Alternative cities to live in the US from the top 3 States in *Population*
----------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

*This notebook will be mainly used for the capstone project*

### *Background*

*Over the past decade, New York, California and Illinois are the fastest growing states in the United States. These are the most populous incorporated states of the United States including designations, city, town, village, borough and municipality. (Based on the Wikipedia source for the year 2019 (*Estimated data https://en.wikipedia.org/wiki/List_of_United_States_cities_by_population)*

*In this project, my focus is on studying about the towns and cities of these states, collecting the data sources of the population and related details about the three states and  analyzing them to find and guide a better place among these three states that have all the satisfying amenities like better workplace, living space and settling with family.*

### *Problem*

*Once the settlements increase in the towns and cities of these three states, the cost of living are skyrocketing. But, due to the work opportunities, we are pushed to select the best out of the situation within these places. The cities like Los Angeles, San Diego and San Jose in California, Hempstead, Brookhaven and Islip in New York and Chicago, Aurora and Rockford in Illinois are the most populous among these states. Through this project, I am trying to give a suggestion for people who would love to settle in these states other than these most populous cities but still avail all or the utmost features of the above cities of these three popular states of USA.*

### *Audience*

*The primary audience of this study might include realtors and potential home buyers/renters in these regions. The findings could also be used by the entrepreneurs looking to open new businesses or even a way of fostering outreach and partnerships among the municipal chambers of commerce.*

### *Data*
 
&emsp;***Sources***

&emsp;&emsp;*To obtain a list of cities of these states, we'll scrape Wikipedia for a list of cities in New York, California and Illinois.  We'll use the Foursquare venue    recommendation to obtain a list of the most popular venues for each city and query location data (latitude/longitude) using the Mapquest Geocoding in order to map all the cities and visualize the clusters. Check out the References for the data sources used in the project.*

&emsp;***Softwares and Tools***

&emsp;&emsp;*We are using Python and the following libraries\Packages to find the solution for the stated problem*

In [1]:
# Install Geocoding library and folium
!pip install geocoder 
!pip install pgeocode

import numpy as np # library to handle data in a vectorized manner
import pandas as pd # library for data analsysis
import geocoder # Geocoding library
import pgeocode as pg

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes 

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests 

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

from sklearn.cluster import KMeans # import k-means from clustering stage

!conda install -c conda-forge folium=0.5.0 --yes 

import folium # map rendering library

print('Libraries imported.')

Solving environment: ...working... done

# All requested packages already installed.

Solving environment: ...working... done

# All requested packages already installed.

Libraries imported.


### *Preparation*

*To obtain a list of cities of these states, we will scrape Wikipedia for a list of cities in New York, California and Illinois. The lists of cities on those pages are structured in tables, so we can easily use Pandas to read in the HTML table and convert it to a dataframe.*

*Will filter\cleanse the source and get only the data what we need*

In [2]:
# Get a list of towns and cities of New York state and prepare a dataframe
tables = pd.read_html("https://en.wikipedia.org/wiki/List_of_towns_in_New_York")
df_nys = tables[1] 
df_nys['State'] = 'NY'
df_nys.columns = ['Town','County','Pop_2010','Land_sq_mi','Water_sq_mi','Coordinates','GEO_ID','ANSI_code','State']
df_nys = df_nys[['Town','State']]
df_nys.head(5)

Town State
0    Adams    NY
1  Addison    NY
2    Afton    NY
3  Alabama    NY
4   Albion    NY

In [3]:
df_nys = df_nys[['Town']]
df_nys.rename(columns={'Town': 'City'}, inplace=True)
df_nys = df_nys.reset_index(drop=True)
df_nys['State']='NY'
df_nys['Latitude']=''
df_nys['Longitude']=''
df_nys

City State Latitude Longitude
0        Adams    NY                   
1      Addison    NY                   
2        Afton    NY                   
3      Alabama    NY                   
4       Albion    NY                   
..         ...   ...      ...       ...
928     Wright    NY                   
929      Yates    NY                   
930       York    NY                   
931  Yorkshire    NY                   
932   Yorktown    NY                   

[933 rows x 4 columns]

In [4]:
df_nys.describe()

City State Latitude Longitude
count        933   933      933       933
unique       923     1        1         1
top     Franklin    NY                   
freq           2   933      933       933

In [5]:
df_nys.shape

(933, 4)

In [6]:
# Get a list of towns and cities of California state and prepare a dataframe
tables = pd.read_html("https://en.wikipedia.org/wiki/List_of_cities_and_towns_in_California",header=1)
df_cas = tables[1] 
df_cas
df_cas['State'] = 'CA'
df_cas.columns = ['Name','Type','County','Pop_2010','Land_sq_mi','Land_km','Incorporated','State']
df_cas = df_cas[['Name','State']]
df_cas.head(5)

Name State
0      Adelanto    CA
1  Agoura Hills    CA
2       Alameda    CA
3        Albany    CA
4      Alhambra    CA

In [7]:
df_cas = df_cas[['Name']]
df_cas.rename(columns={'Name': 'City'}, inplace=True)
df_cas = df_cas.reset_index(drop=True)
df_cas['State']='CA'
df_cas['Latitude']=''
df_cas['Longitude']=''
df_cas

City State Latitude Longitude
0        Adelanto    CA                   
1    Agoura Hills    CA                   
2         Alameda    CA                   
3          Albany    CA                   
4        Alhambra    CA                   
..            ...   ...      ...       ...
477    Yountville    CA                   
478         Yreka    CA                   
479     Yuba City    CA                   
480       Yucaipa    CA                   
481  Yucca Valley    CA                   

[482 rows x 4 columns]

In [8]:
df_cas.describe()

City State Latitude Longitude
count             482   482      482       482
unique            482     1        1         1
top     Rolling Hills    CA                   
freq                1   482      482       482

In [9]:
df_cas.shape

(482, 4)

In [10]:
# Get a list of towns and cities of Illinois state and prepare a dataframe
tables = pd.read_html("https://en.wikipedia.org/wiki/List_of_municipalities_in_Illinois")
df_ils = tables[0] 
df_ils['State'] = 'IL'
df_ils.columns = ['Name','Type','Pop_2010','Country','State']
df_ils = df_ils[['Name','State']]
df_ils.head(5)

Name State
0    Abingdon    IL
1  Addieville    IL
2     Addison    IL
3     Adeline    IL
4      Albany    IL

In [11]:
df_ils = df_ils[['Name']]
df_ils.rename(columns={'Name': 'City'}, inplace=True)
df_ils = df_ils.reset_index(drop=True)
df_ils['State']='IL'
df_ils['Latitude']=''
df_ils['Longitude']=''
df_ils

City State Latitude Longitude
0       Abingdon    IL                   
1     Addieville    IL                   
2        Addison    IL                   
3        Adeline    IL                   
4         Albany    IL                   
...          ...   ...      ...       ...
1294        Yale    IL                   
1295  Yates City    IL                   
1296  Yorkville†    IL                   
1297     Zeigler    IL                   
1298        Zion    IL                   

[1299 rows x 4 columns]

In [12]:
df_ils.describe()

City State Latitude Longitude
count         1299  1299     1299      1299
unique        1297     1        1         1
top     Wilmington    IL                   
freq             2  1299     1299      1299

In [13]:
df_ils.shape

(1299, 4)

##### *Cosolidate three states towns and cities into one*

In [14]:
# Cosolidate three states towns and cities into one
df_ltc = df_nys.copy(deep=True)
df_ltc = df_ltc.append(df_cas)
df_ltc = df_ltc.append(df_ils)
df_ltc.reset_index(inplace=True,drop=True)
df_ltc.shape

(2714, 4)

In [15]:
df_ltc.describe()

City State Latitude Longitude
count      2714  2714     2714      2714
unique     2470     3        1         1
top     Windsor    IL                   
freq          4  1299     2714      2714

In [16]:
df_ltc.to_csv('US_Top_Three_States_LTC_Source.csv', sep=',',index=False)

In [17]:
# Add Mapquest credentials to run the following code
MAPQUEST_KEY = '***Masked***'
MAPQUEST_SECRET = '***Masked***'

In [18]:
# Get Latitude and Longitude of all the cities
for index, row in df_ltc.iterrows():
    location = row['City'] + "," + row['State']
    url = 'https://www.mapquestapi.com/geocoding/v1/address?key={}&inFormat=kvp&outFormat=json&location={}&thumbMaps=false'.format(
    MAPQUEST_KEY, 
    location)
    response = requests.get(url).json()
    df_ltc.at[index,'Latitude'] = response['results'][0]['locations'][0]['latLng']['lat']
    df_ltc.at[index,'Longitude'] = response['results'][0]['locations'][0]['latLng']['lng']
    
df_ltc

City State Latitude Longitude
0          Adams    NY  43.8105  -76.0235
1        Addison    NY  42.1051  -77.2343
2          Afton    NY  42.2295  -75.5245
3        Alabama    NY  43.0964   -78.391
4         Albion    NY  43.2463  -78.1938
...          ...   ...      ...       ...
2709        Yale    IL   39.121  -88.0249
2710  Yates City    IL  40.7787  -90.0146
2711  Yorkville†    IL  41.6414  -88.4469
2712     Zeigler    IL  37.8967  -89.0554
2713        Zion    IL  42.4571  -87.8253

[2714 rows x 4 columns]

In [19]:
df_ltc.to_csv('US_Top_Three_States_LTC.csv', sep=',',index=False)

In [75]:
df_ltc

City State Latitude Longitude
0          Adams    NY  43.8105  -76.0235
1        Addison    NY  42.1051  -77.2343
2          Afton    NY  42.2295  -75.5245
3        Alabama    NY  43.0964   -78.391
4         Albion    NY  43.2463  -78.1938
...          ...   ...      ...       ...
2709        Yale    IL   39.121  -88.0249
2710  Yates City    IL  40.7787  -90.0146
2711  Yorkville†    IL  41.6414  -88.4469
2712     Zeigler    IL  37.8967  -89.0554
2713        Zion    IL  42.4571  -87.8253

[2714 rows x 4 columns]

##### *Map the towns and cities to make sure the location data is correct.*

In [76]:
# Use geopy library to get the latitude and longitude values of Washington State
address = 'New York, USA'

geolocator = Nominatim(user_agent="LTC")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York are 40.7127281, -74.0060152.


In [77]:
# create map of the towns and cities of top 3 US states in population using latitude and longitude values
map_ltc = folium.Map(location=[latitude, longitude], zoom_start=5)

# add markers to map
for lat, lng, name in zip(df_ltc['Latitude'], df_ltc['Longitude'], df_ltc['City']):
    label = '{}'.format(name)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_ltc)  
    
map_ltc

##### *Query the Foursquare API for the top venues of each city.*

In [104]:
# Foursquare Credentials
CLIENT_ID = '***Masked***' # your Foursquare ID
CLIENT_SECRET = '***Masked***' # your Foursquare Secret
VERSION = '20180604' # Foursquare API version

*Test one of the value from the dataframe as a sample test to make sure our intension works as expected*

In [105]:
city_latitude = df_ltc.loc[0, 'Latitude'] # City latitude value
city_longitude = df_ltc.loc[0, 'Longitude'] # City longitude value

city_name = df_ltc.loc[0, 'City'] # Name
city_state = df_ltc.loc[0, 'State'] # State

print('Latitude and longitude values of {}, {} are: {}, {}.'.format(city_name,
                                                               city_state,
                                                               city_latitude, 
                                                               city_longitude))

Latitude and longitude values of Adams, NY are: 43.810509, -76.023503.


In [106]:
# Get the top 100 venues within the default city radius
LIMIT = 50 # limit of number of venues returned by Foursquare API

# create URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    city_latitude, 
    city_longitude, 
    LIMIT)

results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5f1a731e4d24b71550d7a897'},
 'response': {'suggestedRadius': 10000,
  'headerLocation': 'Adams',
  'headerFullLocation': 'Adams',
  'headerLocationGranularity': 'city',
  'totalResults': 18,
  'suggestedBounds': {'ne': {'lat': 43.872071266174316,
    'lng': -75.8997738104248},
   'sw': {'lat': 43.72862529754639, 'lng': -76.14784998107909}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4da369e0c6e96ea834cae85d',
       'name': "Dunkin'",
       'location': {'address': '48 W Church St',
        'lat': 43.81008982996243,
        'lng': -76.03116655863579,
        'labeledLatLngs': [{'label': 'display',
          'lat': 43.81008982996243,
          'lng': -76.03116655863579}],
        'distance': 617,
        'postalCode': '13605',
   

*Function to extract the category of a given venue.*

In [107]:
# function to extract the category 

def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

*Structure the returned venue data into a dataframe and filter based on category.*

In [108]:
# Clean the data and structure it as a dataframe

from pandas import json_normalize # tranform JSON file into a pandas dataframe

venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues = nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name         categories        lat        lng
0          Dunkin'         Donut Shop  43.810090 -76.031167
1     Gram's Diner              Diner  43.808869 -76.024474
2   Dollar General     Discount Store  43.824685 -76.022466
3  Stewart's Shops  Convenience Store  43.820641 -76.022106
4           SUBWAY     Sandwich Place  43.821680 -76.022698

*Function to iterate the venue data for all towns and cities in the dataframe.*

In [112]:
# function to repeat the same process to all cities

def getNearbyVenues(names, latitudes, longitudes, radius=500, LIMIT=100):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['City', 
                  'City Latitude', 
                  'City Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [114]:
# Run the function on each city and store in new dataframe

# Note: The Foursquare API has a limit of 950 Regular API Calls per day and 50 Premium API Calls per day for Sandbox Tier Accounts. 
ltc_venues = getNearbyVenues(names=df_ltc['City'],
                            latitudes=df_ltc['Latitude'],
                            longitudes=df_ltc['Longitude'])

Adams
Addison
Afton
Alabama
Albion
Albion
Alden
Alexander
Alexandria
Alfred
Allegany
Allen
Alma
Almond
Altona
Amboy
Amenia
Amherst
Amity
Amsterdam
Ancram
Andes
Andover
Angelica
Annsville
Antwerp
Arcade
Arcadia
Argyle
Arietta
Arkwright
Ashford
Ashland
Ashland
Athens
Attica
Au Sable
Augusta
Aurelius
Aurora
Austerlitz
Ava
Avoca
Avon
Babylon
Bainbridge
Baldwin
Ballston
Bangor
Barker
Barre
Barrington
Barton
Batavia
Bath
Bedford
Beekman
Beekmantown
Belfast
Bellmont
Bennington
Benson
Benton
Bergen
Berkshire
Berlin
Berne
Bethany
Bethel
Bethlehem
Big Flats
Binghamton
Birdsall
Black Brook
Bleecker
Blenheim
Blooming Grove
Bolivar
Bolton
Bombay
Boonville
Boston
Bovina
Boylston
Bradford
Brandon
Brant
Brasher
Bridgewater
Brighton
Brighton
Bristol
Broadalbin
Brookfield
Brookhaven
Broome
Brownville
Brunswick
Brutus
Burke
Burlington
Burns
Busti
Butler
Butternuts
Byron
Cairo
Caledonia
Callicoon
Cambria
Cambridge
Camden
Cameron
Camillus
Campbell
Canaan
Canadice
Canajoharie
Canandaigua
Candor
Caneadea
Can

In [115]:
# Store the data for future need of reload the dataframe
ltc_venues.to_csv('US_Top3_State_Pop_Town_City_Venues.csv', sep=',',index=False)

*Check the dataframe of towns and cities venues to make sure everything looks in order*

In [189]:
# Check the size of dataframe
print(ltc_venues.shape)
ltc_venues.head()

(24366, 7)


City  City Latitude  City Longitude               Venue  Venue Latitude  \
0  Adams      43.810509      -76.023503        Gram's Diner       43.808869   
1  Adams      43.810509      -76.023503   Hometown Pizzeria       43.809169   
2  Adams      43.810509      -76.023503          Jreck Subs       43.809642   
3  Adams      43.810509      -76.023503             Mercers       43.809660   
4  Adams      43.810509      -76.023503  Dp Bartlett & Sons       43.814521   

   Venue Longitude              Venue Category  
0       -76.024474                       Diner  
1       -76.024676                 Pizza Place  
2       -76.021185              Sandwich Place  
3       -76.021007           Convenience Store  
4       -76.023847  Construction & Landscaping

In [317]:
ltc_venues

City  City Latitude  City Longitude  \
0      Adams      43.810509      -76.023503   
1      Adams      43.810509      -76.023503   
2      Adams      43.810509      -76.023503   
3      Adams      43.810509      -76.023503   
4      Adams      43.810509      -76.023503   
...      ...            ...             ...   
24361   Zion      42.457095      -87.825306   
24362   Zion      42.457095      -87.825306   
24363   Zion      42.457095      -87.825306   
24364   Zion      42.457095      -87.825306   
24365   Zion      42.457095      -87.825306   

                                          Venue  Venue Latitude  \
0                                  Gram's Diner       43.808869   
1                             Hometown Pizzeria       43.809169   
2                                    Jreck Subs       43.809642   
3                                       Mercers       43.809660   
4                            Dp Bartlett & Sons       43.814521   
...                                         ...             ...   
24361                                 Dog House       42.454251   
24362                      Star Lite Restaurant       42.453511   
24363                                  Starlite       42.453465   
24364              Starlight Country Restaurant       42.453400   
24365  Randy Nebel - State Farm Insurance Agent       42.453063   

       Venue Longitude              Venue Category  
0           -76.024474                       Diner  
1           -76.024676                 Pizza Place  
2           -76.021185              Sandwich Place  
3           -76.021007           Convenience Store  
4           -76.023847  Construction & Landscaping  
...                ...                         ...  
24361       -87.825905               Hot Dog Joint  
24362       -87.825190                  Restaurant  
24363       -87.825065              Breakfast Spot  
24364       -87.825200                  Restaurant  
24365       -87.825258            Insurance Office  

[24366 rows x 7 columns]

*Let's list down the towns and cities.*

*Have tested different limits and found that a city requires at least about 10 venue entries in order to have an adequate venue "profile" for meaningful clustering results with 
other towns and cities. Given that, we'll drop towns and cities with fewer than 10 venues for the remainder of this analysis*

In [348]:
# Limit Venues in the towns and cities where more than 10 only   

ltc_filter_venue = ltc_venues
ltc_filter_venue['count'] = ltc_filter_venue.groupby('City')['City'].transform('count')
ltc_seleted_venue = ltc_filter_venue[ltc_filter_venue['count'] > 10]
ltc_seleted_venue

City  City Latitude  City Longitude  \
5      Addison      42.105085      -77.234330   
6      Addison      42.105085      -77.234330   
7      Addison      42.105085      -77.234330   
8      Addison      42.105085      -77.234330   
9      Addison      42.105085      -77.234330   
...        ...            ...             ...   
24361     Zion      42.457095      -87.825306   
24362     Zion      42.457095      -87.825306   
24363     Zion      42.457095      -87.825306   
24364     Zion      42.457095      -87.825306   
24365     Zion      42.457095      -87.825306   

                                          Venue  Venue Latitude  \
5                                Dollar General       42.103854   
6                                      7-Eleven       42.105657   
7                                    Main Grill       42.106368   
8                                   Sugar Creek       42.105698   
9                                     China Wok       42.106501   
...                                         ...             ...   
24361                                 Dog House       42.454251   
24362                      Star Lite Restaurant       42.453511   
24363                                  Starlite       42.453465   
24364              Starlight Country Restaurant       42.453400   
24365  Randy Nebel - State Farm Insurance Agent       42.453063   

       Venue Longitude      Venue Category  count  
5           -77.235717      Discount Store     29  
6           -77.233682   Convenience Store     29  
7           -77.234366                 Bar     29  
8           -77.233795         Gas Station     29  
9           -77.233801  Chinese Restaurant     29  
...                ...                 ...    ...  
24361       -87.825905       Hot Dog Joint     26  
24362       -87.825190          Restaurant     26  
24363       -87.825065      Breakfast Spot     26  
24364       -87.825200          Restaurant     26  
24365       -87.825258    Insurance Office     26  

[18127 rows x 8 columns]

In [349]:
ltc_seleted_venue.shape

(18127, 8)

In [350]:
ltc_seleted_venue.describe()

City Latitude  City Longitude  Venue Latitude  Venue Longitude  \
count   18127.000000    18127.000000    18127.000000     18127.000000   
mean       38.499299     -103.276589       38.499369      -103.276622   
std         3.418062       19.973629        3.418104        19.973579   
min        32.044340     -124.143149       32.041002      -124.147529   
25%        34.414144     -121.002435       34.415077      -121.000166   
50%        38.349747     -117.575764       38.348790      -117.571679   
75%        41.822259      -87.831558       41.822474       -87.828521   
max        48.229950       34.750991       48.234416        34.752563   

              count  
count  18127.000000  
mean      40.138412  
std       23.811840  
min       11.000000  
25%       21.000000  
50%       34.000000  
75%       56.000000  
max      121.000000

In [353]:
# Check total venues per city
grouped = ltc_seleted_venue.groupby('City').count()
print('Actual count of cities: {}'.format(len(grouped.index)))

# Drop cities with inadequate amount of venue data (they skew the clustering results)
grouped = grouped[grouped.Venue > 10]
list(grouped.index.values)
ltc_venues = ltc_seleted_venue[~ltc_seleted_venue['City'].isin(list(grouped.index.values))]
grouped2 = ltc_seleted_venue.groupby('City').count()

print('Cities with more than 10 venues: {}'.format(len(grouped2.index)))

Actual count of cities: 644
Cities with more than 10 venues: 644


*Unique categories among the returned venues*

In [354]:
print('There are {} unique categories.'.format(len(ltc_seleted_venue['Venue Category'].unique())))

There are 462 unique categories.


### *Methodology*

*We have collected the data what we need to analyze*

*We will use unsupervised machine learning algorithm called k-means clustering that enables us to partition observations into a specified number of clusters in order to discover underlying patterns.* 

*With the data, we will find the the top 5 venue categories for each city (based on occurances in the dataset), and use that as each city's vector profile for finding similarities with other cities.*

*First we need to calculate the average frequency for each venue category across each city. We can quickly do this with a Pandas dataframe by converting each venue category into a boolean (yes/no) column.*

In [365]:
# one hot encoding
ltc_selected_onehot = pd.get_dummies(ltc_seleted_venue[['Venue Category']], prefix="", prefix_sep="")

# Add city column back to dataframe
ltc_selected_onehot['City'] = ltc_seleted_venue['City'] 

# move city column to the first column
fixed_columns = [ltc_selected_onehot.columns[-1]] + list(ltc_selected_onehot.columns[:-1])
ltc_selected_onehot = ltc_selected_onehot[fixed_columns]

# Check size of new dataframe
ltc_selected_onehot.shape

(18127, 462)

In [366]:
ltc_selected_onehot.head(100)

Zoo  ATM  Accessories Store  Adult Boutique  Advertising Agency  \
5      0    0                  0               0                   0   
6      0    0                  0               0                   0   
7      0    0                  0               0                   0   
8      0    0                  0               0                   0   
9      0    0                  0               0                   0   
..   ...  ...                ...             ...                 ...   
187    0    0                  0               0                   0   
188    0    0                  0               0                   0   
189    0    0                  0               0                   0   
190    0    0                  0               0                   0   
191    0    0                  0               0                   0   

     Afghan Restaurant  African Restaurant  American Restaurant  Antique Shop  \
5                    0                   0                    0             0   
6                    0                   0                    0             0   
7                    0                   0                    0             0   
8                    0                   0                    0             0   
9                    0                   0                    0             0   
..                 ...                 ...                  ...           ...   
187                  0                   0                    0             0   
188                  0                   0                    0             0   
189                  0                   0                    1             0   
190                  0                   0                    0             0   
191                  0                   0                    0             0   

     Aquarium  ...  Weight Loss Center  Whisky Bar  Wine Bar  Wine Shop  \
5           0  ...                   0           0         0          0   
6           0  ...                   0           0         0          0   
7           0  ...                   0           0         0          0   
8           0  ...                   0           0         0          0   
9           0  ...                   0           0         0          0   
..        ...  ...                 ...         ...       ...        ...   
187         0  ...                   0           0         0          0   
188         0  ...                   0           0         0          0   
189         0  ...                   0           0         0          0   
190         0  ...                   0           0         0          0   
191         0  ...                   0           0         0          0   

     Winery  Wings Joint  Women's Store  Xinjiang Restaurant  Yoga Studio  \
5         0            0              0                    0            0   
6         0            0              0                    0            0   
7         0            0              0                    0            0   
8         0            0              0                    0            0   
9         0            0              0                    0            0   
..      ...          ...            ...                  ...          ...   
187       0            0              0                    0            0   
188       0            0              0                    0            0   
189       0            0              0                    0            0   
190       0            0              0                    0            0   
191       0            0              0                    0            0   

     Yoshoku Restaurant  
5                     0  
6                     0  
7                     0  
8                     0  
9                     0  
..                  ...  
187                   0  
188                   0  
189                   0  
190                   0  
191                   0  

[100 rows x 462 columns]

*The dataframe shape looks correct, as the column count matches the number of unique venue categories we calculated earlier.*
*We will group rows by city mean of frequency for each category.*

In [367]:
ltc_selected_grouped = ltc_selected_onehot.groupby('City').mean().reset_index()
ltc_selected_grouped

City  Zoo       ATM  Accessories Store  Adult Boutique  \
0         Addison  0.0  0.000000                0.0             0.0   
1         Alameda  0.0  0.000000                0.0             0.0   
2          Albany  0.0  0.000000                0.0             0.0   
3          Albion  0.0  0.000000                0.0             0.0   
4      Alexandria  0.0  0.000000                0.0             0.0   
..            ...  ...       ...                ...             ...   
639   Yorba Linda  0.0  0.000000                0.0             0.0   
640    Yountville  0.0  0.000000                0.0             0.0   
641         Yreka  0.0  0.090909                0.0             0.0   
642  Yucca Valley  0.0  0.000000                0.0             0.0   
643          Zion  0.0  0.000000                0.0             0.0   

     Advertising Agency  Afghan Restaurant  African Restaurant  \
0                   0.0           0.000000                 0.0   
1                   0.0           0.011905                 0.0   
2                   0.0           0.000000                 0.0   
3                   0.0           0.000000                 0.0   
4                   0.0           0.000000                 0.0   
..                  ...                ...                 ...   
639                 0.0           0.000000                 0.0   
640                 0.0           0.000000                 0.0   
641                 0.0           0.000000                 0.0   
642                 0.0           0.000000                 0.0   
643                 0.0           0.000000                 0.0   

     American Restaurant  Antique Shop  ...  Weight Loss Center  Whisky Bar  \
0               0.000000      0.000000  ...                 0.0         0.0   
1               0.023810      0.000000  ...                 0.0         0.0   
2               0.000000      0.000000  ...                 0.0         0.0   
3               0.000000      0.000000  ...                 0.0         0.0   
4               0.117647      0.000000  ...                 0.0         0.0   
..                   ...           ...  ...                 ...         ...   
639             0.000000      0.000000  ...                 0.0         0.0   
640             0.054054      0.000000  ...                 0.0         0.0   
641             0.090909      0.000000  ...                 0.0         0.0   
642             0.058824      0.058824  ...                 0.0         0.0   
643             0.000000      0.000000  ...                 0.0         0.0   

     Wine Bar  Wine Shop  Winery  Wings Joint  Women's Store  \
0    0.000000   0.000000     0.0     0.000000            0.0   
1    0.023810   0.023810     0.0     0.011905            0.0   
2    0.000000   0.015152     0.0     0.000000            0.0   
3    0.000000   0.000000     0.0     0.000000            0.0   
4    0.000000   0.000000     0.0     0.000000            0.0   
..        ...        ...     ...          ...            ...   
639  0.000000   0.000000     0.0     0.000000            0.0   
640  0.108108   0.000000     0.0     0.000000            0.0   
641  0.000000   0.000000     0.0     0.000000            0.0   
642  0.000000   0.000000     0.0     0.000000            0.0   
643  0.000000   0.000000     0.0     0.000000            0.0   

     Xinjiang Restaurant  Yoga Studio  Yoshoku Restaurant  
0                    0.0          0.0                 0.0  
1                    0.0          0.0                 0.0  
2                    0.0          0.0                 0.0  
3                    0.0          0.0                 0.0  
4                    0.0          0.0                 0.0  
..                   ...          ...                 ...  
639                  0.0          0.0                 0.0  
640                  0.0          0.0                 0.0  
641                  0.0          0.0                 0.0  
642                  0.0          0.0            

In [368]:
ltc_selected_grouped.shape

(644, 462)

##### *Find the five most common venues for each city.*

In [370]:
num_top_venues = 5

for city in ltc_selected_grouped['City']:
    print("------------------"+city+"------------------")
    temp = ltc_selected_grouped[ltc_selected_grouped['City'] == city].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

------------------Addison------------------
                venue  freq
0         Pizza Place  0.14
1      Ice Cream Shop  0.10
2  Italian Restaurant  0.07
3         Video Store  0.03
4  Mexican Restaurant  0.03


------------------Alameda------------------
                venue  freq
0     Thai Restaurant  0.04
1      Sandwich Place  0.04
2         Pizza Place  0.02
3     Bubble Tea Shop  0.02
4  Mexican Restaurant  0.02


------------------Albany------------------
                  venue  freq
0           Pizza Place  0.08
1       Thai Restaurant  0.05
2           Coffee Shop  0.05
3  Gym / Fitness Center  0.03
4           Gas Station  0.03


------------------Albion------------------
            venue  freq
0     Pizza Place   0.2
1            Bank   0.1
2  Sandwich Place   0.1
3      Donut Shop   0.1
4     Post Office   0.1


------------------Alexandria------------------
                 venue  freq
0          Pizza Place  0.12
1               Resort  0.12
2  American Restaurant  

*The raw data looks good. Now let's sort and structure it for further processing.*

In [371]:
# Function to sort venues in decscending order
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [372]:
# Create a dataframe with top 5 venues for each city
num_top_venues = 5

indicators = ['st', 'nd', 'rd']

# Create columns according to number of top venues
columns = ['City']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# Create a new dataframe
cities_venues_sorted = pd.DataFrame(columns=columns)
cities_venues_sorted['City'] = ltc_selected_grouped['City']

for ind in np.arange(ltc_selected_grouped.shape[0]):
    cities_venues_sorted.iloc[ind, 1:] = return_most_common_venues(ltc_selected_grouped.iloc[ind, :], num_top_venues)

cities_venues_sorted.head()

City 1st Most Common Venue 2nd Most Common Venue  \
0     Addison           Pizza Place        Ice Cream Shop   
1     Alameda       Thai Restaurant        Sandwich Place   
2      Albany           Pizza Place           Coffee Shop   
3      Albion           Pizza Place           Post Office   
4  Alexandria                Resort   American Restaurant   

  3rd Most Common Venue 4th Most Common Venue    5th Most Common Venue  
0    Italian Restaurant       Thai Restaurant  New American Restaurant  
1    Chinese Restaurant           Coffee Shop          Bubble Tea Shop  
2       Thai Restaurant        Sandwich Place         Sushi Restaurant  
3        Sandwich Place            Donut Shop             Liquor Store  
4           Pizza Place            Steakhouse      Sporting Goods Shop

In [431]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)
pd.set_option('display.max_colwidth', 1)

cites_venus = cities_venues_sorted
cites_venus

Cluster Labels                    City            1st Most Common Venue  \
0    2               Addison                 Pizza Place                       
1    3               Alameda                 Thai Restaurant                   
2    3               Albany                  Pizza Place                       
3    2               Albion                  Pizza Place                       
4    5               Alexandria              Resort                            
5    0               Alfred                  Bar                               
6    1               Algonquin               Park                              
7    3               Alhambra                Bakery                            
8    3               Aliso Viejo             Fast Food Restaurant              
9    2               Alton                   Pharmacy                          
10   6               Alturas                 Hotel                             
11   3               American Canyon         Pharmacy                          
12   3               Amherst                 Furniture / Home Store            
13   3               Anaheim                 Mexican Restaurant                
14   5               Antioch                 American Restaurant               
15   4               Apple Valley            Park                              
16   2               Arcadia                 Racetrack                         
17   3               Arcata                  Pizza Place                       
18   3               Arlington Heights       Italian Restaurant                
19   0               Arroyo Grande           Bar                               
20   3               Artesia                 Indian Restaurant                 
21   4               Arvin                   Fast Food Restaurant              
22   0               Athens                  Bar                               
23   5               Atwater                 American Restaurant               
24   5               Auburn                  Burger Joint                      
25   6               Aurora                  Mexican Restaurant                
26   3               Avalon                  Hotel                             
27   0               Avon                    Bar                               
28   6               Azusa                   Pharmacy                          
29   3               Babylon                 American Restaurant               
30   0               Bakersfield             Bar                               
31   2               Baldwin                 Pharmacy                          
32   6               Baldwin Park            Mexican Restaurant                
33   2               Barrington              Pizza Place                       
34   6               Bartlett                Other Repair Shop                 
35   3               Batavia                 Coffee Shop                       
36   5               Bedford                 Deli / Bodega                     
37   6               Bell                    Mexican Restaurant                
38   6               Belleville†             Mexican Restaurant                
39   3               Bellflower              Bank                              
40   3               Belmont                 Sandwich Place                    
41   5               Belvedere               Italian Restaurant                
42   3               Benicia                 Deli / Bodega                     
43   4               Bensenville             Fried Chicken Joint               
44   3               Berkeley                Coffee Shop                       
45   2               Berwyn                  Pizza Place                       
46   4               Big Bear Lake           Fast Food Restaurant              
47   0               Binghamton              Bar                               
48   6               Bishop                  Mexican Restaurant                
49   

*Apply the K-means clustering algorithm.* 
*I found the clusters to be most meaningful and interesting with around k=7.*
*The output of the K-means algorithm is an array of cluster assignments for each row in our dataframe.*

In [402]:
# Run K-means to break up into clusters
kclusters = 7

ltc_selected_grouped_clustering = ltc_selected_grouped.drop('City', 1)

# Run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(ltc_selected_grouped_clustering)

# Check cluster labels generated for each row in the dataframe
kmeans.labels_[0:600]

array([2, 3, 3, 2, 5, 0, 1, 3, 3, 2, 6, 3, 3, 3, 5, 4, 2, 3, 3, 0, 3, 4,
       0, 5, 5, 6, 3, 0, 6, 3, 0, 2, 6, 2, 6, 3, 5, 6, 6, 3, 3, 5, 3, 4,
       3, 2, 4, 0, 6, 2, 3, 4, 4, 3, 0, 3, 3, 2, 3, 2, 1, 6, 6, 3, 3, 0,
       3, 2, 4, 5, 5, 3, 4, 5, 6, 5, 0, 4, 3, 2, 3, 5, 5, 3, 2, 0, 0, 3,
       5, 3, 0, 3, 6, 3, 4, 3, 3, 2, 2, 3, 3, 6, 0, 5, 5, 4, 3, 1, 4, 4,
       6, 2, 3, 3, 3, 1, 4, 6, 6, 4, 2, 3, 3, 4, 2, 3, 3, 6, 5, 3, 2, 5,
       5, 3, 4, 3, 2, 6, 6, 6, 0, 5, 5, 3, 2, 3, 2, 2, 3, 6, 6, 3, 6, 3,
       3, 4, 5, 5, 3, 3, 3, 3, 6, 6, 4, 3, 6, 6, 3, 1, 4, 0, 5, 6, 4, 3,
       4, 3, 4, 3, 6, 3, 4, 5, 0, 4, 3, 3, 1, 0, 5, 2, 6, 3, 3, 3, 2, 3,
       3, 2, 3, 3, 3, 3, 2, 1, 2, 6, 2, 3, 3, 2, 4, 6, 3, 0, 2, 3, 3, 3,
       3, 5, 3, 5, 3, 2, 6, 5, 3, 2, 0, 5, 3, 3, 2, 3, 0, 5, 5, 3, 3, 6,
       5, 6, 6, 6, 1, 4, 0, 3, 5, 2, 2, 3, 3, 1, 0, 6, 3, 3, 3, 2, 3, 6,
       2, 2, 5, 4, 2, 3, 5, 4, 1, 3, 2, 2, 5, 3, 3, 5, 2, 0, 2, 2, 3, 4,
       2, 4, 0, 2, 3, 6, 0, 0, 6, 6, 2, 3, 2, 5, 3,

In [410]:
cities_venues_sorted.columns

Index(['Cluster Labels', 'City', '1st Most Common Venue',
       '2nd Most Common Venue', '3rd Most Common Venue',
       '4th Most Common Venue', '5th Most Common Venue'],
      dtype='object')

*Plug the cluster labels into our dataframe and also combine city location data. With all this info we are ready to visualize.*

In [411]:
df_ltc

City State Latitude Longitude
0          Adams    NY  43.8105  -76.0235
1        Addison    NY  42.1051  -77.2343
2          Afton    NY  42.2295  -75.5245
3        Alabama    NY  43.0964   -78.391
4         Albion    NY  43.2463  -78.1938
...          ...   ...      ...       ...
2709        Yale    IL   39.121  -88.0249
2710  Yates City    IL  40.7787  -90.0146
2711  Yorkville†    IL  41.6414  -88.4469
2712     Zeigler    IL  37.8967  -89.0554
2713        Zion    IL  42.4571  -87.8253

[2714 rows x 4 columns]

In [429]:
# Create dataframe that includes the cluster and top 5 venues

pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)
pd.set_option('display.max_colwidth', 1)

df_temp = df_ltc

# Merge Venues on the List of Towns and Cities with Main List of Townsand Cities to add latitude/longitude for each city
cites_venus_data = df_temp.join(cities_venues_sorted.set_index('City'), on='City')

# Drop cities with no venue data
cites_venus_data = cites_venus_data.dropna()

cites_venus_data

City State Latitude Longitude  Cluster Labels  \
1     Addison                 NY    42.1051 -77.2343   2.0              
4     Albion                  NY    43.2463 -78.1938   2.0              
5     Albion                  NY    43.2463 -78.1938   2.0              
8     Alexandria              NY    44.3368 -75.919    5.0              
9     Alfred                  NY    42.2547 -77.7904   0.0              
17    Amherst                 NY    42.9791 -78.7993   3.0              
27    Arcadia                 NY    43.0466 -77.0953   2.0              
34    Athens                  NY    42.2601 -73.8089   0.0              
39    Aurora                  NY    42.754  -76.7024   6.0              
43    Avon                    NY    42.9127 -77.7459   0.0              
44    Babylon                 NY    40.6958 -73.3257   3.0              
46    Baldwin                 NY    40.663  -73.6107   2.0              
51    Barrington              NY    42.5503 -77.0564   2.0              
53    Batavia                 NY    42.9969 -78.186    3.0              
55    Bedford                 NY    41.2026 -73.6422   5.0              
71    Binghamton              NY    42.0987 -75.9125   0.0              
89    Brighton                NY    42.9911 -78.8372   2.0              
90    Brighton                NY    42.9911 -78.8372   2.0              
93    Brookfield              NY    42.8129 -75.3175   1.0              
105   Byron                   NY    43.0829 -78.0648   0.0              
107   Caledonia               NY    42.9732 -77.8552   2.0              
114   Campbell                NY    42.2329 -77.1969   3.0              
118   Canandaigua             NY    42.8875 -77.2825   5.0              
122   Canton                  NY    44.5956 -75.1692   6.0              
136   Catskill                NY    42.2176 -73.8649   5.0              
138   Cazenovia               NY    42.9299 -75.8509   3.0              
146   Chatham                 NY    42.4407 -73.5575   0.0              
149   Cheektowaga             NY    42.9071 -78.7543   3.0              
154   Chester                 NY    41.3622 -74.2742   5.0              
155   Chester                 NY    41.3622 -74.2742   5.0              
157   Chili                   NY    43.1165 -77.8045   3.0              
158   Cicero                  NY    43.1755 -76.1193   4.0              
164   Clarkstown              NY    41.1474 -73.9894   2.0              
168   Clayton                 NY    44.2408 -76.0885   3.0              
170   Clifton                 NY    40.62   -74.0775   3.0              
171   Clifton Park            NY    42.8638 -73.7782   6.0              
172   Clinton                 NY    43.0486 -75.378    0.0              
173   Clinton                 NY    43.0486 -75.378    0.0              
181   Coldspring              NY    41.42   -73.9548   3.0              
185   Colton                  NY    44.553  -74.9395   4.0              
188   Concord                 NY    42.5353 -78.7314   6.0              
197   Corinth                 NY    43.2444 -73.8317   2.0              
198   Corning                 NY    42.1412 -77.0531   3.0              
200   Cortlandt               NY    41.2048 -73.8851   3.0              
209   Cuba                    NY    42.219  -78.2766   2.0              
213   Dansville               NY    42.5597 -77.6947   2.0              
224   Deerfield               NY    43.1802 -75.149    3.0              
225   Deerpark                NY    40.7574 -73.3266   2.0              
226   Delaware                NY    41.768  -75.0573   5.0              
246   East Hampton            NY    40.9647 -72.1947   5.0              
248   East Rochester          NY    43.1144 -77.4905   3.0              
249   Eastchester             NY    40.9559 -73.8138   2.0              
252   Eden                    NY    42.6524 -78.8969   2.0              
260   Ellery                  NY    42.1599 -79.3932   5.0              
262   Ell

In [430]:
cites_venus_data.shape

(771, 10)

### *Results and discussion*

##### *Will use the Python Folium library to render clusters, using a distinct color for each.*

In [421]:
# Create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=6)

# Set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# Add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(cites_venus_data['Latitude'], cites_venus_data['Longitude'], cites_venus_data['City'], cites_venus_data['Cluster Labels']):
    cluster = int(cluster)
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

*The results are prety good, lets analyze the data and understand*

##### *Cluster 0: Outliers*

*This cluster consists 65 outlier towns and cities from the three states. We can see from the venue data and and most of primary venues are Bar.*

In [437]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)
pd.set_option('display.max_colwidth', 1)

cites_venus_data.loc[cites_venus_data['Cluster Labels'] == 0, cites_venus_data.columns[[0] + [1] + list(range(5, cites_venus_data.shape[1]))]]

City State   1st Most Common Venue 2nd Most Common Venue  \
9     Alfred         NY    Bar                     Café                   
34    Athens         NY    Bar                     American Restaurant    
43    Avon           NY    Bar                     Gas Station            
71    Binghamton     NY    Bar                     Café                   
105   Byron          NY    Convenience Store       Sandwich Place         
146   Chatham        NY    Bar                     Fast Food Restaurant   
172   Clinton        NY    Bar                     Sandwich Place         
173   Clinton        NY    Bar                     Sandwich Place         
318   Geneva         NY    Bar                     Pizza Place            
417   Islip          NY    Bar                     Food Court             
471   Lisle          NY    Pizza Place             Bar                    
479   Lockport       NY    Bar                     Restaurant             
480   Lodi           NY    Bar                     Playground             
654   Peru           NY    Bar                     Pizza Place            
672   Plattsburgh    NY    Bar                     Restaurant             
677   Pomfret        NY    Bar                     Pizza Place            
793   Springfield    NY    Bar                     Sandwich Place         
804   Sterling       NY    Bar                     Fast Food Restaurant   
818   Sweden         NY    Bar                     Pizza Place            
829   Tonawanda      NY    Bar                     Pharmacy               
831   Trenton        NY    Bar                     American Restaurant    
877   Watertown      NY    Sandwich Place          Bar                    
914   Wilmington     NY    American Restaurant     Bar                    
949   Arroyo Grande  CA    Bar                     Pizza Place            
959   Bakersfield    CA    Bar                     Dive Bar               
1003  Chico          CA    Bar                     Mexican Restaurant     
1163  Lodi           CA    Bar                     Playground             
1215  Nevada City    CA    Bar                     American Restaurant    
1290  Roseville      CA    Bar                     Pizza Place            
1369  Truckee        CA    Bar                     American Restaurant    
1377  Upland         CA    Bar                     American Restaurant    
1463  Athens         IL    Bar                     American Restaurant    
1472  Avon           IL    Bar                     Gas Station            
1540  Breese         IL    Bar                     Diner                  
1577  Byron          IL    Convenience Store       Sandwich Place         
1598  Carbondale     IL    Pizza Place             Bar                    
1621  Champaign      IL    Bar                     Pub                    
1626  Chatham        IL    Bar                     Fast Food Restaurant   
1747  East Dubuque   IL    Bar                     American Restaurant    
1821  Forest Park    IL    Bar                     Park                   
1839  Galesburg†     IL    Bar                     Mexican Restaurant     
1914  Harvard        IL    Bar                     Pizza Place            
1936  Highwood       IL    Bar                     Coffee Shop            
1953  Homewood       IL    Bar                     Café                   
2017  Kewanee        IL    Furniture / Home Store  American Restaurant    
2059  Lemont         IL    Bar                     American Restaurant    
2076  Lisle          IL    Pizza Place             Bar                    
2083  Lockport       IL    Bar                     Restaurant             
2123  Marengo        IL    American Restaurant     Bar                    
2176  Millstadt      IL    Bar                     Gas Station            
2195  Morton         IL    Pizza Place             Bar                    
2265  North Utica    IL    Bar                     Gourmet Shop           
2270  O'Fallon       IL    Bar          

##### *Cluster 1: Vacation destinations*

*Cluster 1 classified by hotels/resorts, restaurants and nightlife (bars, breweries, etc).*
*Many of the cities on this list are vacation destinations and/or popular weekend getaway spots.*

In [444]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)
pd.set_option('display.max_colwidth', 1)

cites_venus_data.loc[cites_venus_data['Cluster Labels'] == 1, cites_venus_data.columns[[0] + [1] + list(range(5, cites_venus_data.shape[1]))]]

City State 1st Most Common Venue 2nd Most Common Venue  \
93    Brookfield        NY    Park                  Irish Pub              
317   Geneseo           NY    Park                  Bar                    
413   Inlet             NY    Park                  Coffee Shop            
488   Lyons             NY    Bar                   Park                   
606   Olean             NY    Steakhouse            Bar                    
674   Plymouth          NY    Post Office           Convenience Store      
736   Salina            NY    Park                  Coffee Shop            
875   Waterford         NY    Park                  Café                   
904   Wheatland         NY    Park                  Bar                    
1016  Colfax            CA    Pizza Place           Train Station          
1029  Cotati            CA    Park                  Bar                    
1074  Folsom            CA    Park                  Zoo                    
1096  Gridley           CA    Post Office           Bar                    
1258  Plymouth          CA    Post Office           Convenience Store      
1350  South Lake Tahoe  CA    Park                  Coffee Shop            
1389  Waterford         CA    Park                  Café                   
1398  Wheatland         CA    Park                  Bar                    
1424  Algonquin         IL    Park                  River                  
1549  Brookfield        IL    Park                  Irish Pub              
1660  Colfax            IL    Pizza Place           Train Station          
1844  Geneseo           IL    Park                  Bar                    
1893  Gridley           IL    Post Office           Bar                    
2005  Kankakee†         IL    Music Venue           Bar                    
2046  Lake Zurich       IL    Park                  Breakfast Spot         
2101  Lyons             IL    Bar                   Park                   
2325  Park Forest       IL    Bank                  Movie Theater          
2360  Plymouth          IL    Post Office           Convenience Store      

        3rd Most Common Venue 4th Most Common Venue     5th Most Common Venue  
93    Pizza Place              Sports Bar            Business Service          
317   American Restaurant      Pizza Place           Café                      
413   Grocery Store            Bookstore             Ice Cream Shop            
488   Sandwich Place           Fast Food Restaurant  Supermarket               
606   Convenience Store        Café                  Mexican Restaurant        
674   New American Restaurant  Hotel                 Diner                     
736   American Restaurant      Supermarket           Thai Restaurant           
875   American Restaurant      Chinese Restaurant    Sandwich Place            
904   Bridge                   River                 Café                      
1016  Park                     Food                  Grocery Store             
1029  Music Store              Breakfast Spot        Bike Rental / Bike Share  
1074  Astrologer               Liquor Store          Mexican Restaurant        
1096  Park                     Baseball Field        Home Service              
1258  New American Restaurant  Hotel                 Diner                     
1350  Toy / Game Store         Pizza Place           Sporting Goods Shop       
1389  American Restaurant      Chinese Restaurant    Sandwich Place            
1398  Bridge                   River                 Café                      
1424  Intersection             Gas Station           Bar                       
1549  Pizza Place              Sports Bar            Business Service          
1660  Park                     Food                  Grocery Store             
1844  American Restaurant      Pizza Place           Café                      
1893  Park                     Baseball Field        Home Service              
2005  Train Station            Sandwich Place    

##### *Cluster 2: : Restaurant towns and cities*

*Pizza place is common among nearly all of the cities in this cluster. It looks like Pizza Place, Mexican Restaurant, Chinese Restaurant, American Restaurant, 
and Bar are all grouping together here. The towns and cities on this list tend to be larger than bedroom communities, 
but somewhat smaller than major urban centers.*

In [447]:
# Cluster 2
cites_venus_data.loc[cites_venus_data['Cluster Labels'] == 2, cites_venus_data.columns[[0] + [1] + list(range(5, cites_venus_data.shape[1]))]]

City State 1st Most Common Venue   2nd Most Common Venue  \
1     Addison             NY    Pizza Place           Ice Cream Shop           
4     Albion              NY    Pizza Place           Post Office              
5     Albion              NY    Pizza Place           Post Office              
27    Arcadia             NY    Racetrack             Hotel                    
46    Baldwin             NY    Pharmacy              Bar                      
51    Barrington          NY    Pizza Place           Sandwich Place           
89    Brighton            NY    Pizza Place           Optical Shop             
90    Brighton            NY    Pizza Place           Optical Shop             
107   Caledonia           NY    Pizza Place           Gas Station              
164   Clarkstown          NY    Pizza Place           Coffee Shop              
197   Corinth             NY    Pizza Place           Convenience Store        
209   Cuba                NY    Pharmacy              Bar                      
213   Dansville           NY    Discount Store        Café                     
225   Deerpark            NY    Pizza Place           African Restaurant       
249   Eastchester         NY    Pizza Place           Pharmacy                 
252   Eden                NY    Pizza Place           Liquor Store             
322   German Flatts       NY    Convenience Store     Pet Store                
349   Groton              NY    Pizza Place           Hobby Shop               
365   Hancock             NY    Pharmacy              Diner                    
389   Highlands           NY    Donut Shop            Pizza Place              
428   Johnstown           NY    Pizza Place           Hot Dog Joint            
446   Lancaster           NY    Pizza Place           Plaza                    
447   Lansing             NY    Pizza Place           Bar                      
462   Lewiston            NY    Pizza Place           Coffee Shop              
465   Liberty             NY    Pizza Place           Bar                      
473   Little Falls        NY    Gym / Fitness Center  Bakery                   
499   Mamakating          NY    Pizza Place           Ice Cream Shop           
519   Mendon              NY    Italian Restaurant    Pizza Place              
553   Mount Morris        NY    Food                  Pizza Place              
557   Naples              NY    Hotel                 Breakfast Spot           
589   North Dansville     NY    Discount Store        Café                     
641   Parma               NY    Grocery Store         Insurance Office         
648   Penfield            NY    Pizza Place           Italian Restaurant       
649   Perinton            NY    Pizza Place           Ice Cream Shop           
673   Pleasant Valley     NY    Bar                   Pizza Place              
701   Red Hook            NY    Pizza Place           Convenience Store        
791   Sparta              NY    Bank                  Pizza Place              
836   Tupper Lake         NY    Donut Shop            Restaurant               
857   Victor              NY    Brewery               Pizza Place              
868   Wappinger           NY    Pizza Place           Pharmacy                 
873   Warwick             NY    Bank                  Furniture / Home Store   
887   Wellsville          NY    Pizza Place           Pharmacy                 
907   Whitehall           NY    Café                  Museum                   
922   Wolcott             NY    Market                Pizza Place              
947   Arcadia             CA    Racetrack             Hotel                    
998   Carpinteria         CA    Pizza Place           Sandwich Place           
1090  Glendora            CA    Pizza Place           Breakfast Spot           
1093  Grand Terrace       CA    Pizza Place           Sandwich Place           
1113  Hollister           CA    Pizza Place           Fast Food Restaurant     
1135  La Habra      

##### *Cluster 3: Coffee shop towns and cities*

*In addition to coffee shops being the prevalent venue type, the cities in this cluster are charaterized by a diverse set of ammenities, indicative of larger urban centers.*

In [450]:
# Cluster 3 
cites_venus_data.loc[cites_venus_data['Cluster Labels'] == 3, cites_venus_data.columns[[0] + [1] + list(range(5, cites_venus_data.shape[1]))]]

City State      1st Most Common Venue  \
17    Amherst                 NY    Furniture / Home Store      
44    Babylon                 NY    American Restaurant         
53    Batavia                 NY    Coffee Shop                 
114   Campbell                NY    Mexican Restaurant          
138   Cazenovia               NY    Café                        
149   Cheektowaga             NY    Intersection                
157   Chili                   NY    Flower Shop                 
168   Clayton                 NY    Harbor / Marina             
170   Clifton                 NY    Bus Stop                    
181   Coldspring              NY    Café                        
198   Corning                 NY    Café                        
200   Cortlandt               NY    Deli / Bodega               
224   Deerfield               NY    Coffee Shop                 
248   East Rochester          NY    Italian Restaurant          
266   Elmira                  NY    Pub                         
285   Fishkill                NY    Italian Restaurant          
296   Frankfort               NY    Pet Store                   
302   Fremont                 NY    Grocery Store               
303   Fremont                 NY    Grocery Store               
330   Goshen                  NY    Deli / Bodega               
338   Greece                  NY    Coffee Shop                 
343   Greenport               NY    Boat or Ferry               
360   Hamilton                NY    Sandwich Place              
374   Harrison                NY    Italian Restaurant          
383   Hempstead               NY    Supermarket                 
391   Hinsdale                NY    Bakery                      
393   Homer                   NY    Market                      
407   Huntington              NY    Mexican Restaurant          
436   Kingston                NY    Italian Restaurant          
452   Le Roy                  NY    Post Office                 
487   Lyndon                  NY    Women's Store               
498   Malta                   NY    Bar                         
500   Mamaroneck              NY    Italian Restaurant          
503   Manlius                 NY    Chinese Restaurant          
527   Middletown              NY    Bowling Alley               
530   Milo                    NY    Café                        
531   Milton                  NY    Ice Cream Shop              
539   Monroe                  NY    Bank                        
552   Mount Kisco             NY    Restaurant                  
566   New Castle              NY    Café                        
572   New Paltz               NY    Mexican Restaurant          
584   Niles                   NY    Korean Restaurant           
590   North East              NY    Pizza Place                 
608   Oneonta                 NY    Italian Restaurant          
612   Orange                  NY    Coffee Shop                 
613   Orangetown              NY    Bar                         
615   Orchard Park            NY    Coffee Shop                 
620   Ossining                NY    Café                        
622   Oswego                  NY    Pizza Place                 
633   Palatine                NY    Convenience Store           
644   Pawling                 NY    Pizza Place                 
668   Pittsford               NY    New American Restaurant     
670   Plainfield              NY    Park                        
683   Potsdam                 NY    Italian Restaurant          
685   Poughkeepsie            NY    Deli / Bodega               
706   Rhinebeck               NY    Furniture / Home Store      
710   Richmond                NY    Italian Restaurant          
716   Rochester               NY    Coffee Shop                 
723   Rosendale               NY    Bus Station                 
733   Rye                     NY    Bank                        
744   Saratoga                NY    Convenience Store      

##### *Cluster 4: Fast food towns and cities*

*The unifying characteristic among these cities is that Fast Food Restaurant is the prominent venue type. These are smaller cities and bedroom communities that tend to be located between larger cities with more ammenties. At first glance, a "Fast food towns and cities" might not seem particularly attractive, but this cluster deserves further exploration for prospective home buyers looking for more seclusion and lower real estate prices.*

In [453]:
# Cluster 4
cites_venus_data.loc[cites_venus_data['Cluster Labels'] == 4, cites_venus_data.columns[[0] + [1] + list(range(5, cites_venus_data.shape[1]))]]

City State 1st Most Common Venue   2nd Most Common Venue  \
158   Cicero             NY    Fast Food Restaurant  Mexican Restaurant       
185   Colton             NY    Pizza Place           Breakfast Spot           
306   Fulton             NY    Fast Food Restaurant  Deli / Bodega            
468   Lincoln            NY    Sandwich Place        Breakfast Spot           
742   Santa Clara        NY    Fast Food Restaurant  Indian Restaurant        
946   Apple Valley       CA    Park                  Fast Food Restaurant     
951   Arvin              CA    Fast Food Restaurant  Pizza Place              
972   Big Bear Lake      CA    Fast Food Restaurant  Sporting Goods Shop      
987   Calexico           CA    Fast Food Restaurant  Chinese Restaurant       
996   Carlsbad           CA    Fast Food Restaurant  Park                     
1018  Colton             CA    Pizza Place           Breakfast Spot           
1021  Compton            CA    Fast Food Restaurant  Bakery                   
1036  Daly City          CA    Fast Food Restaurant  Sandwich Place           
1075  Fontana            CA    Fast Food Restaurant  Mexican Restaurant       
1079  Foster City        CA    Fast Food Restaurant  Café                     
1085  Galt               CA    Chinese Restaurant    Fast Food Restaurant     
1101  Hanford            CA    Bank                  Fast Food Restaurant     
1127  Irwindale          CA    Fast Food Restaurant  Mexican Restaurant       
1145  Laguna Hills       CA    Fast Food Restaurant  Sandwich Place           
1158  Lincoln            CA    Sandwich Place        Breakfast Spot           
1183  Marina             CA    Mexican Restaurant    Fast Food Restaurant     
1185  Marysville         CA    Mexican Restaurant    Sandwich Place           
1201  Montebello         CA    Fast Food Restaurant  American Restaurant      
1220  Norwalk            CA    Fast Food Restaurant  Pizza Place              
1221  Novato             CA    Bank                  Bakery                   
1249  Pico Rivera        CA    Fast Food Restaurant  Mexican Restaurant       
1279  Ridgecrest         CA    Fast Food Restaurant  Hotel                    
1296  San Bernardino     CA    Sandwich Place        Insurance Office         
1319  Sanger             CA    Fast Food Restaurant  Mexican Restaurant       
1322  Santa Clara        CA    Fast Food Restaurant  Indian Restaurant        
1355  Suisun City        CA    Fast Food Restaurant  Sandwich Place           
1384  Visalia            CA    Fast Food Restaurant  Italian Restaurant       
1394  West Sacramento    CA    Bank                  Burger Joint             
1399  Whittier           CA    Sandwich Place        Hardware Store           
1508  Bensenville        IL    Fried Chicken Joint   Pizza Place              
1525  Blue Island        IL    Fast Food Restaurant  Bar                      
1534  Bourbonnais        IL    Fast Food Restaurant  Chinese Restaurant       
1591  Campton Hills      IL    Bar                   Ice Cream Shop           
1640  Cicero             IL    Fast Food Restaurant  Mexican Restaurant       
1652  Coal City          IL    Pizza Place           Fast Food Restaurant     
1666  Compton            IL    Fast Food Restaurant  Bakery                   
1675  Countryside        IL    Mexican Restaurant    Fast Food Restaurant     
1686  Crystal Lake       IL    Fast Food Restaurant  American Restaurant      
1724  Dixon†             IL    Convenience Store     Fast Food Restaurant     
1769  Elk Grove Village  IL    Sandwich Place        Mexican Restaurant       
1792  Evergreen Park     IL    Fast Food Restaurant  Bank                     
1827  Fox River Grove    IL    Music Venue           Bowling Alley            
1831  Franklin Park      IL    Hotel                 Pizza Place              
1835  Fulton             IL    Fast Food Restaurant  Deli / Bodega            
2045  Lake Villa         IL    Video Store           Fast Food Restau

##### *Cluster 5: More Restaurants*

*The yield for the final cluster was a couple more restaurants towns and cities, more are in New York state.*

In [466]:
# Cluster 5
cites_venus_data.loc[cites_venus_data['Cluster Labels'] == 5, cites_venus_data.columns[[0] + [1] + list(range(5, cites_venus_data.shape[1]))]]

City State   1st Most Common Venue    2nd Most Common Venue  \
8     Alexandria      NY    Resort                  American Restaurant       
55    Bedford         NY    Deli / Bodega           Café                      
118   Canandaigua     NY    Pub                     Brewery                   
136   Catskill        NY    Café                    Diner                     
154   Chester         NY    Bar                     Italian Restaurant        
155   Chester         NY    Bar                     Italian Restaurant        
226   Delaware        NY    American Restaurant     Bar                       
246   East Hampton    NY    Italian Restaurant      Bakery                    
260   Ellery          NY    American Restaurant     Boutique                  
262   Ellicottville   NY    American Restaurant     Sporting Goods Shop       
386   Herkimer        NY    Italian Restaurant      Fast Food Restaurant      
388   Highland        NY    American Restaurant     Convenience Store         
390   Hillsdale       NY    Convenience Store       Wine Shop                 
401   Horseheads      NY    Italian Restaurant      Dive Bar                  
402   Hounsfield      NY    Italian Restaurant      Harbor / Marina           
420   Jackson         NY    Furniture / Home Store  American Restaurant       
443   Lake George     NY    American Restaurant     Motel                     
453   Lebanon         NY    Arts & Entertainment    American Restaurant       
507   Marcellus       NY    American Restaurant     Bank                      
542   Montgomery      NY    American Restaurant     Deli / Bodega             
543   Montour         NY    Bed & Breakfast         Bank                      
546   Moreau          NY    Park                    Convenience Store         
564   New Berlin      NY    Italian Restaurant      Business Service          
567   New Hartford    NY    Italian Restaurant      Indian Restaurant         
601   Norwich         NY    American Restaurant     Deli / Bodega             
604   Ogden           NY    Burger Joint            Brewery                   
625   Otsego          NY    American Restaurant     Italian Restaurant        
630   Owego           NY    American Restaurant     Café                      
632   Oyster Bay      NY    American Restaurant     Ice Cream Shop            
645   Pelham          NY    American Restaurant     Moving Target             
715   Riverhead       NY    BBQ Joint               American Restaurant       
746   Saugerties      NY    American Restaurant     Ice Cream Shop            
762   Seneca Falls    NY    American Restaurant     History Museum            
853   Vernon          NY    American Restaurant     Post Office               
866   Walton          NY    Discount Store          American Restaurant       
871   Warrensburg     NY    Sandwich Place          Discount Store            
872   Warsaw          NY    American Restaurant     Convenience Store         
884   Webb            NY    American Restaurant     Bar                       
897   Westfield       NY    American Restaurant     Italian Restaurant        
945   Antioch         CA    American Restaurant     Italian Restaurant        
954   Atwater         CA    American Restaurant     Fried Chicken Joint       
955   Auburn          CA    Burger Joint            American Restaurant       
968   Belvedere       CA    Italian Restaurant      Harbor / Marina           
989   Calimesa        CA    American Restaurant     Fast Food Restaurant      
991   Calistoga       CA    Hotel                   Bed & Breakfast           
995   Capitola        CA    American Restaurant     Bar                       
1012  Cloverdale      CA    Deli / Bodega           Hotel                     
1013  Clovis          CA    Italian Restaurant      Mexican Restaurant        
1040  Del Mar         CA    Italian Restaurant      Mexican Restaurant        
1106  Hemet           CA    American Restaurant     Bar           

### ***Conclusion***

*From the three states, namely New York, California and Illinois, we have a total of 2714 cities, out of which only 644 cities are listed with the Foursquare venue data. A Foursquare query of venues in these cities yielded 24,366 venues, however, we need to filter out cities with fewer than 10 venues, as their profile later proved insufficient for meaningful clustering. After filtering out those cities, only 644 remained.*

*The 644 cities used in the final analysis represented 18127 venues and 462 unique venue types. We used the k-means clustering algorithm to group them into six distinct clusters, however only four of those clusters were truly meaningful in terms of revealing insights among our dataset that we could use to answer the original question of our problem search. 
How can the residents of these states identify similar cities as prospective places to move? The results of our analysis certainly provide an idea for these residents who are planning for moving to other cities with similar life benefits.*

*Throughout the process of this study, we uncovered limitations in comprehensively addressing the problem at hand. We also found interesting patterns among the refined dataset of larger cities with an adequate amount of Foursquare venue data.*

*Next step in the process might be to supplement the data to cluster cities with additional sources like average home price, population size etc. so as to retain and cluster a full list of the cities with finer - grained grouping patterns for cities with ample Foursquare venue data.*

### ***Recommendations***

*It is clearly known that people, investors and real estate persons can focus on these towns and cities. We found that these cities are having all the needed facilities with the available data from the Foursquare API. We would like to have more data and analysis to fine tune the model for better results.*

### ***References***

&emsp;*[1.] https://en.wikipedia.org/wiki/List_of_United_States_cities_by_population*

&emsp;*[2.] https://en.wikipedia.org/wiki/List_of_towns_in_New_York*

&emsp;*[3.] https://en.wikipedia.org/wiki/List_of_cities_and_towns_in_California*

&emsp;*[4.] https://en.wikipedia.org/wiki/List_of_municipalities_in_Illinois*

&emsp;*[5.] https://api.foursquare.com/v2/venues/explore?*

&emsp;*[6.] https://www.mapquestapi.com/geocoding/v1/address?*